In [2]:
import pandas as pd
import numpy as np
import os
import imp
import telephone_analysis
import srilm
import roark
import glob
import shutil
import scipy.stats
imp.reload(telephone_analysis)
%load_ext rpy2.ipython
import rpy2.robjects.lib.ggplot2 as ggplot2
import kenlm

In [3]:
import glob

from os.path import join, exists
import pickle

import transformers
from transformers import GPT2LMHeadModel, GPT2Tokenizer, BertForMaskedLM, BertTokenizer, BartForConditionalGeneration, BartTokenizer

import new_models
from new_models import prep_probs

import load_runs

In [6]:
all_runs = load_runs.load_runs()

all_runs.loc[all_runs.user != "0"].shape[0]
len(np.unique(all_runs.loc[all_runs.user != "0"].user))

0    0
1    5
2    4
3    3
4    1
Name: index, dtype: int64


/home/nwong/chompsky/serial_chain/telephone-analysis-public/load_runs.py:22: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  all_runs = pd.concat(dfs)


266

# Word-Level Language Modeling Results

In [44]:
# index in the LM corresponds to the response: user_candidate_transcription. 3192: last input

In [5]:
lm = {}

In [6]:
bnc_knn_lm = srilm.LM("LMs/BNC_merged.LM", lower=True)

In [8]:
lm['bnc_unigram'] =  [telephone_analysis.getSRILMprob(x, {}, bnc_knn_lm, mode='single_word', unigram=True) for x in all_runs['user_candidate_transcription']]

In [9]:
lm['bnc_trigram'] =  [telephone_analysis.getSRILMprob(x, {}, bnc_knn_lm, mode='single_word', unigram = False) for x in all_runs['user_candidate_transcription']]

In [10]:
lm['roark_scores'] = roark.parse([str(i) for i in all_runs['user_candidate_transcription']], 
    '/home/nwong/utils/incremental-top-down-parser',
                          numWorkers=24, mode='single_word')

Input contains 3193 sentences
Input contains 1982 unique sentences
Finished external parsing


/home/nwong/chompsky/serial_chain/telephone-analysis-public/roark.py:235: FutureWarning: read_table is deprecated, use read_csv instead.
  pfix_df = pd.read_table(StringIO('\n'.join(y)), sep=' ', header=None, names = ['prefix','word']+colnames)
/home/nwong/chompsky/serial_chain/telephone-analysis-public/telephone-env-3/lib/python3.7/site-packages/pandas/io/parsers.py:702: UserWarning: Duplicate names specified. This will raise an error in the future.
  return _read(filepath_or_buffer, kwds)


In [12]:
lm['big_lm_scores'] = telephone_analysis.getBigLMscores(all_runs['user_candidate_transcription'], 'big_lm',
    'big_lm_cache', colname='BigLM_probability', lm_1b_dir='/home/nwong/python/lm_1b', mode='single_word')

Big LM call:
cd /home/nwong/python/lm_1b && source bin/activate && bazel-bin/lm_1b/lm_1b_eval --mode eval_sentences --pbtxt data/graph-2016-09-10.pbtxt --vocab_file data/vocab-2016-09-10.txt --eval_dir /home/nwong/chompsky/serial_chain/telephone-analysis-public/big_lm --ckpt 'data/ckpt-*'
2


In [138]:
m = kenlm.Model('LMs/deepspeech_5gram.binary')
lm['kenlm_scores'] = [telephone_analysis.getKenLMProb(x, m, mode='single_word') for x in all_runs['user_candidate_transcription']]

# For consistency in the filtering.
lm['kenlm_scores'] = [df.rename(columns = {'words' : 'word'}) for df in lm['kenlm_scores']] 

In [33]:

for lm_name in lm:

    filtered_df_list = list(map(prep_probs.filter_eos_punct_df, lm[lm_name]))
    lm[lm_name] = filtered_df_list
    # Filter out all of the </S> and "."
    #   before the word comparison, to ensure alignment.
    
    # Note that for this to work with kenlm, the "words" column must be renamed to "word".
    # Additionally there can't be a second "kenlm_probability" column.
    assert(len(lm[lm_name]) == all_runs.shape[0])
    

bnc_unigram
bnc_trigram
roark_scores
big_lm_scores
kenlm_scores


In [34]:
RESULTS_FOLDER = './intermediate_results/new_models_probs'

from new_models import prep_probs
import importlib
import align_prep_words

importlib.reload(prep_probs)

model_names = ['gpt2_normal', 'gpt2_medium', 'bert', 'bart']

tokenizers = {
    'gpt2': GPT2Tokenizer.from_pretrained('gpt2'),
    'bert': BertTokenizer.from_pretrained("bert-large-uncased-whole-word-masking"),
    'bart': BartTokenizer.from_pretrained("facebook/bart-base"),
}


In [37]:
# Note: bnc_unigram words are listed as the "words" of the transformers,
# because of the filtering on bad tokens.

# this means that this also filters out the capitalization, since none of the bnc_unigram_words are capitalized.

word_list = [df['word'].values.tolist() for df in lm['bnc_unigram']]

transformer_names = ['gpt2_normal', 'gpt2_medium', 'bert', 'bart']
tokenizer_names = ['gpt2', 'gpt2', 'bert', 'bart']

for model_name, tokenizer_name in zip(transformer_names, tokenizer_names):

    print(f'Processing model name: {model_name}')
    
    raw_scores = prep_probs.load_word_scores(model_name, RESULTS_FOLDER) # This is not filtering properly.
    lm[f'{model_name}_scores'] = align_prep_words.align_model_word_dfs(raw_scores,
                                                                       tokenizers[tokenizer_name],
                                                                       word_list)

gpt2
Processing model name: gpt2_normal
       word      prob
0      Each  0.000269
1      Ġnon  0.000262
2   fiction  0.011790
3     Ġbook  0.438744
4      Ġhas  0.057975
5        Ġa  0.289296
6     Ġcall  0.000068
7   Ġnumber  0.000363
8       Ġon  0.043549
9      Ġits  0.095197
10   Ġspine  0.051601
Index: 0
collapse ['each', 'non', 'fiction', 'book', 'has', 'a', 'call', 'number', 'on', 'its', 'spine']
['each', 'nonfiction', 'book', 'has', 'a', 'call', 'number', 'on', 'its', 'spine']
[-3.5703540948773504, None, -0.35778880118207934, -1.2367606257775672, -0.5386575246216043, -4.164424229668198, -3.4398320265759232, -1.361023212680492, -1.0213747339578825, -1.287339936885073]
collapse ['each', 'non', 'fiction', 'book', 'has', 'a', 'call', 'number', 'in', 'its', 'spine']
['each', 'non', 'fiction', 'book', 'has', 'a', 'call', 'number', 'in', 'its', 'spine']
[-3.5703540948773504, -3.581757880300356, -4.859724430647189, -0.7231748245200208, -1.1290658964567049, -0.5203305827936678, -4.174

['someone', 'said', 'you', 'might', 'know', 'me']
[-4.076158434718445, -1.5111130770307137, -1.6354688043967571, -1.7906122255599355, -2.1487593656655313, -1.3237015068259956]
collapse ['someone', 'said', 'he', 'might', 'run']
['someone', 'said', 'he', 'might', 'run']
[-4.076158434718445, -1.5111130770307137, -1.6581590421484251, -2.0701197736923485, -2.2283833094064174]
collapse ['someone', 'said', 'you', 'might', 'run']
['someone', 'said', 'you', 'might', 'run']
[-4.076158434718445, -1.5111130770307137, -1.6354688043967571, -1.7906122255599355, -2.464811692110044]
collapse ['the', 'chase', 'leads', 'across', 'a', 'field', 'toward', 'a', 'nearby', 'farm']
['the', 'chase', 'leads', 'across', 'a', 'field', 'toward', 'a', 'nearby', 'farm']
[-1.4236626276000017, -4.555040239223463, -2.879539405989715, -2.687232253877029, -0.9765131057322816, -1.7726235798772214, -2.3805829711800874, -0.622318086541745, -2.4372603070103733, -2.2548480346893323]
collapse ['the', 'chase', 'leads', 'across', 

['the', 'fly', 'was', 'next', 'to', 'the', 'boy', 'on', 'the', 'paper']
[-1.4236626276000017, -4.7814815537373585, -1.8634644644848248, -3.458247393493857, -0.3129619105768093, -0.5619829769808974, -3.2345428684001787, -1.5097822717936826, -0.17719017442979848, -3.334993464609793]
collapse ['the', 'fly', 'was', 'next', 'to', 'the', 'boil', 'on', 'the', 'paper']
['the', 'fly', 'was', 'next', 'to', 'the', 'boil', 'on', 'the', 'paper']
[-1.4236626276000017, -4.7814815537373585, -1.8634644644848248, -3.458247393493857, -0.3129619105768093, -0.5619829769808974, -4.193471786884016, -2.1588430299273047, -0.3992397706128278, -3.6074512871827458]
collapse ['the', 'fly', 'was', 'next', 'to', 'the', 'coil', 'on', 'the', 'paper']
['the', 'fly', 'was', 'next', 'to', 'the', 'coil', 'on', 'the', 'paper']
[-1.4236626276000017, -4.7814815537373585, -1.8634644644848248, -3.458247393493857, -0.3129619105768093, -0.5619829769808974, -4.391063295601616, -1.5201341494436316, -0.18609679366719364, -3.1924550

['the', 'discovery', 'of', 'oil', 'has', 'caused', 'many', 'cities', 'to', 'run']
[-1.4236626276000017, -3.563779092995754, -0.2123078132137356, -2.759767793571439, -2.254079053553719, -1.7444954108368604, -1.8233164200139647, -2.6884136781733745, -0.30866278426220084, -2.713792041389662]
collapse ['the', 'discovery', 'of', 'oil', 'has', 'caused', 'many', 'cities', 'to', 'run']
['the', 'discovery', 'of', 'oil', 'has', 'caused', 'many', 'cities', 'to', 'run']
[-1.4236626276000017, -3.563779092995754, -0.2123078132137356, -2.759767793571439, -2.254079053553719, -1.7444954108368604, -1.8233164200139647, -2.6884136781733745, -0.30866278426220084, -2.713792041389662]
collapse ['the', 'discovery', 'of', 'oil', 'has', 'caused', 'many', 'cities', 'to', 'run']
['the', 'discovery', 'of', 'oil', 'has', 'caused', 'many', 'cities', 'to', 'run']
[-1.4236626276000017, -3.563779092995754, -0.2123078132137356, -2.759767793571439, -2.254079053553719, -1.7444954108368604, -1.8233164200139647, -2.68841367

collapse ['now', 'the', 'plane', 'is', 'due', '1000', 'miles', 'north']
['now', 'the', 'plane', 'is', 'due', '1000', 'miles', 'north']
[-2.866981377029175, -1.6528543083282292, -4.024323730325628, -0.6814419932128535, -2.4271170070586763, -6.226388496954717, -0.23332124463710696, -1.4268421223498449]
collapse ['now', 'the', 'plane', 'is', 'due', 'one', 'thousand', 'miles', 'north']
['now', 'the', 'plane', 'is', 'due', 'one', 'thousand', 'miles', 'north']
[-2.866981377029175, -1.6528543083282292, -4.024323730325628, -0.6814419932128535, -2.4271170070586763, -4.625166191186135, -3.435794027165032, -0.29486352395488485, -1.3437831757673269]
collapse ['now', 'the', 'plane', 'is', 'due', '1000', 'miles', 'more']
['now', 'the', 'plane', 'is', 'due', '1000', 'miles', 'more']
[-2.866981377029175, -1.6528543083282292, -4.024323730325628, -0.6814419932128535, -2.4271170070586763, -6.226388496954717, -0.23332124463710696, -3.8377941505615607]
collapse ['now', 'the', 'plane', 'was', 'one', 'thousa

...

collapse ['i', 'am', 'sorry', 'to', 'be', 'informed', 'of', 'text', 'matters', 'at', 'cost', 'co']
['i', 'am', 'sorry', 'to', 'be', 'informed', 'of', 'text', 'matters', 'at', 'cost', 'co']
[-0.6140224255716734, -0.3805317868471514, -1.8890960635194465, -0.8786511643627806, -0.9414423900850033, -2.8640664743288804, -0.38124477188313166, -5.635231417632724, -5.37757559247601, -1.4389210892952973, -4.077660411158853, -5.026797537841077]
collapse ['i', 'am', 'sorry', 'to', 'be', 'informed', 'of', 'text', 'matters', 'at', 'cost', 'co']
['i', 'am', 'sorry', 'to', 'be', 'informed', 'of', 'text', 'matters', 'at', 'cost', 'co']
[-0.6140224255716734, -0.3805317868471514, -1.8890960635194465, -0.8786511643627806, -0.9414423900850033, -2.8640664743288804, -0.38124477188313166, -5.635231417632724, -5.37757559247601, -1.4389210892952973, -4.077660411158853, -5.026797537841077]
collapse ['i', 'am', 'sorry', 'to', 'be', 'informed', 'of', 'text', 'matters', 'at', 'cost', 'co']
['i', 'am', 'sorry', 'to'

collapse ['m', 'ops', 'are', 'for', 'cleaning', 'things', 'to', 'scratch']
['mops', 'are', 'for', 'cleaning', 'things', 'to', 'scratch']
[None, -0.7676914996372058, -1.937306322209273, -2.1090275717608526, -1.9304426124339413, -2.1975076198202936, -3.196160159646119]
collapse ['b', 'obs', 'are', 'for', 'cleaning', 'and', 'things', 'to', 'scratch', '']
['bobs', 'are', 'for', 'cleaning', 'and', 'things', 'to', 'scratch']
[None, -0.7107586374463015, -1.234055830635681, -2.050078158591727, -0.8133138969126463, -2.7337760886497158, -1.0786615080639983, -3.7600258343353]
collapse ['log', 's', 'are', 'for', 'cleaning', 'and', 'things', 'to', 'scratch']
['logs', 'are', 'for', 'cleaning', 'and', 'things', 'to', 'scratch']
[None, -0.7897433536084131, -1.1774420586104708, -3.3694935793682115, -0.7888241117642374, -2.994615343317348, -1.0971137202490044, -4.6920111102198225]
collapse ['log', 's', 'are', 'for', 'cleaning', 'and', 'things', 'to', 'scratch']
['logs', 'are', 'for', 'cleaning', 'and', 

collapse ['two', 'forms', 'of', 'theater', 'are', 'drama', 'and', 'comedy']
['two', 'forms', 'of', 'theater', 'are', 'drama', 'and', 'comedy']
[-0.6362289397416251, -1.7254629399887427, -0.007908154149711868, -1.9003959556612364, -0.5952950050428278, -1.8330144507740624, -0.05693991477825776, -1.3863098848032611]
collapse ['two', 'forms', 'of', 'theater', 'are', 'drama', 'and', 'comedy']
['two', 'forms', 'of', 'theater', 'are', 'drama', 'and', 'comedy']
[-0.6362289397416251, -1.7254629399887427, -0.007908154149711868, -1.9003959556612364, -0.5952950050428278, -1.8330144507740624, -0.05693991477825776, -1.3863098848032611]
collapse ['two', 'forms', 'of', 'theater', 'are', 'drama', 'and', 'comedy']
['two', 'forms', 'of', 'theater', 'are', 'drama', 'and', 'comedy']
[-0.6362289397416251, -1.7254629399887427, -0.007908154149711868, -1.9003959556612364, -0.5952950050428278, -1.8330144507740624, -0.05693991477825776, -1.3863098848032611]
collapse ['two', 'forms', 'of', 'theater', 'are', 'dram

['the', 'contract', 'is', 'an', 'agreement', 'which', 'is', 'enforced', 'by', 'law']
[-0.7883570900430737, -2.126098015161249, -0.3343074010160293, -0.7082259373314476, -0.9000911208492259, -1.1454844117036855, -0.18006032912477246, -2.430954031552282, -0.3575378869827067, -1.5179967276127044]
collapse ['the', 'contract', 'is', 'an', 'agreement', 'which', 'is', 'enforced', 'by', 'law']
['the', 'contract', 'is', 'an', 'agreement', 'which', 'is', 'enforced', 'by', 'law']
[-0.7883570900430737, -2.126098015161249, -0.3343074010160293, -0.7082259373314476, -0.9000911208492259, -1.1454844117036855, -0.18006032912477246, -2.430954031552282, -0.3575378869827067, -1.5179967276127044]
collapse ['the', 'contract', 'is', 'an', 'agreement', 'which', 'is', 'enforced', 'by', 'law']
['the', 'contract', 'is', 'an', 'agreement', 'which', 'is', 'enforced', 'by', 'law']
[-0.7883570900430737, -2.126098015161249, -0.3343074010160293, -0.7082259373314476, -0.9000911208492259, -1.1454844117036855, -0.18006032

collapse ['he', 'could', 'see', 'that', 'they', 'were', 'determined', 'to', 'turn', 'back']
['he', 'could', 'see', 'that', 'they', 'were', 'determined', 'to', 'turn', 'back']
[-2.0777673868948217, -0.5110836324314098, -0.7731326600329635, -0.5344304969358584, -0.8991784240145544, -0.09386181632659572, -3.0338344369512775, -0.3082064925927773, -2.170881921506806, -1.2225518355647553]
collapse ['he', 'could', 'see', 'that', 'they', 'were', 'determined', 'to', 'turn', 'back', '']
['he', 'could', 'see', 'that', 'they', 'were', 'determined', 'to', 'turn', 'back']
[-1.992975294822801, -0.44974960286791676, -0.8298319945737647, -0.5404738522773808, -0.903489150802954, -0.09639640916841072, -3.0136401770805525, -0.3210074141349688, -2.0533984516555326, -1.3999885800027363]
collapse ['he', 'could', 'see', 'that', 'they', 'were', 'determined', 'to', 'turn', 'back']
['he', 'could', 'see', 'that', 'they', 'were', 'determined', 'to', 'turn', 'back']
[-2.0777673868948217, -0.5110836324314098, -0.773

In [39]:
# Need to pickle all of the results

DATA_PREP_FOLDER = './intermediate_results/data_prep_logistic'
if not os.path.exists(DATA_PREP_FOLDER):
    os.makedirs(DATA_PREP_FOLDER)
    
for lm_name, lm_data in lm.items():
    print(lm_name)
    load_runs.pickle_logistic_prep(lm_data, lm_name, DATA_PREP_FOLDER)

bnc_unigram
Saved per-word scores to ./intermediate_results/data_prep_logistic/bnc_unigram_predictions.txt.
bnc_trigram
Saved per-word scores to ./intermediate_results/data_prep_logistic/bnc_trigram_predictions.txt.
roark_scores
Saved per-word scores to ./intermediate_results/data_prep_logistic/roark_scores_predictions.txt.
big_lm_scores
Saved per-word scores to ./intermediate_results/data_prep_logistic/big_lm_scores_predictions.txt.
kenlm_scores
Saved per-word scores to ./intermediate_results/data_prep_logistic/kenlm_scores_predictions.txt.
gpt2_normal_scores
Saved per-word scores to ./intermediate_results/data_prep_logistic/gpt2_normal_scores_predictions.txt.
gpt2_medium_scores
Saved per-word scores to ./intermediate_results/data_prep_logistic/gpt2_medium_scores_predictions.txt.
bert_scores
Saved per-word scores to ./intermediate_results/data_prep_logistic/bert_scores_predictions.txt.
bart_scores
Saved per-word scores to ./intermediate_results/data_prep_logistic/bart_scores_predictio

# Proceed from saved results here

In [7]:
DATA_PREP_FOLDER = './intermediate_results/data_prep_logistic'

model_names = [filename.split('logistic/')[1].split('_predictions.txt')[0]
               for filename in glob.glob(DATA_PREP_FOLDER+'/*')]

lm = {}

for lm_name in model_names:
    raw_scores_path = join(DATA_PREP_FOLDER, f"{lm_name}_predictions.txt")
    # 3/27: https://stackoverflow.com/questions/27745500/how-to-save-a-list-to-a-file-and-read-it-as-a-list-type
    with open(raw_scores_path, 'rb') as f:
        raw_scores = pickle.load(f)
        lm[lm_name] = raw_scores

In [8]:
# sanity check: all sentences in all models must have the same number of tokens in the dataframe
languageModelNames = ['bnc_unigram', 'bnc_trigram', 'roark_scores', 'big_lm_scores', 'kenlm_scores',
                     'gpt2_normal_scores', 'gpt2_medium_scores', 'bert_scores', 'bart_scores']

for i in range(all_runs.shape[0]):
    sentences = [lm[x][i] for x in languageModelNames]
    try:
        numWords = [x.shape[0] for x in sentences]
    except:
        print('Problem counting words')
        import pdb
        pdb.set_trace()
    if not np.allclose(numWords[1:len(numWords)], numWords[0]):
        print('Different number of words')
        import pdb
        pdb.set_trace()

In [9]:
sentence_store = []
for i in range(all_runs.shape[0]):
    # need to rename what is coming out of each language model
    word_store = [] 
    for languageModelName in languageModelNames:
        df = lm[languageModelName][i].copy()
        try:
            df.columns = [languageModelName+'_'+x for x in df.columns]        
        except:
            import pdb
            pdb.set_trace()
        word_store.append(df)
    lms_combined = pd.concat(word_store, axis =1)
    lms_combined['sCounter'] = range(lms_combined.shape[0])
    lms_combined['sentence_index'] = i
    sentence_store.append(lms_combined)
wdf = pd.concat(sentence_store)

In [10]:
wdf['word'] = wdf[u'bnc_unigram_word']

In [11]:
wdf.iloc[0:21] # Nonfiction (two versions: one with non fiction, one with nonfiction)

#wdf.iloc[170:200] # Dietitian index.

bnc_unigram_index  bnc_unigram_prob bnc_unigram_word  bnc_trigram_index  \
0                   0         -3.310068             each                  0   
1                   1         -7.309903       nonfiction                  1   
2                   2         -3.631093             book                  2   
3                   3         -2.600407              has                  3   
4                   4         -1.681165                a                  4   
5                   5         -3.737589             call                  5   
6                   6         -3.321531           number                  6   
7                   7         -2.162270               on                  7   
8                   8         -2.804867              its                  8   
9                   9         -5.034822            spine                  9   
0                   0         -3.310068             each                  0   
1                   1         -5.084593              non                  1   
2                   2         -4.733100          fiction                  2   
3                   3         -3.631093             book                  3   
4                   4         -2.600407              has                  4   
5                   5         -1.681165                a                  5   
6                   6         -3.737589             call                  6   
7                   7         -3.321531           number                  7   
8                   8         -1.746052               in                  8   
9                   9         -2.804867              its                  9   
10                 10         -5.034822            spine                 10   

    bnc_trigram_prob bnc_trigram_word roark_scores_prefix roark_scores_word  \
0          -2.994068             each              pfix:1              each   
1          -8.412464       nonfiction              pfix:2        nonfiction   
2          -3.756868             book              pfix:3              book   
3          -2.253614              has              pfix:4               has   
4          -1.317157                a              pfix:5                 a   
5          -3.763689             call              pfix:6              call   
6          -3.708286           number              pfix:7            number   
7          -2.029635               on              pfix:8                on   
8          -2.394903              its              pfix:9               its   
9          -4.401074            spine             pfix:10             spine   
0          -2.994068             each              pfix:1              each   
1          -5.391007              non              pfix:2               non   
2          -2.624665          fiction              pfix:3           fiction   
3          -4.116251             book              pfix:4              book   
4          -2.253614              has              pfix:5               has   
5          -1.317157                a              pfix:6                 a   
6          -3.763689             call              pfix:7              call   
7          -3.708286           number              pfix:8            number   
8          -1.743438               in              pfix:9                in   
9          -2.384786              its             pfix:10               its   
10         -4.449113            spine             pfix:11             spine   

    roark_scores_prefix.1  roark_scores_srprsl  ...  gpt2_normal_scores_word  \
0                   6.566             2.851578  ...                     each   
1                  18.290             5.091669  ...               nonfiction   
2                  28.519             4.442398  ...                     book   
3                  32.402             1.686800  ...                      has   
4                  35.256             1.239042  ...                        a   
5                  44.218             3.892147

In [ ]:
# Each record is a 'produced' word (user_candidate_transcription) 

# Identifying Deleted and Changed Words

In [ ]:
# for generation n, get the indices of all words that have changed in n+1
# have changed: no longer appear? doesn't handle transpositions
# borrowed the function from the old version of telephone

In [15]:
# Code from the Aggregate Notebook, this prevents an error that says that a "float" is being encoded (i.e. NaN)
for x in ['condition','flag_type','gold_candidate_transcription',
          'gold_comparison_transcription','reason', 'subject_id',
         'upstream_subject_id', 'user_comparison_transcription', 'user_short']:
    all_runs[x] = all_runs[x].fillna(value="none")

In [16]:
all_runs.loc[all_runs.user == "0"].head(5)

chain  character_levdau  check_time condition flag_type  \
0       0               NaN         NaN      none      none   
18      0               NaN         NaN      none      none   
43      0               NaN         NaN      none      none   
66      0               NaN         NaN      none      none   
93      0               NaN         NaN      none      none   

   gold_candidate_transcription gold_comparison_transcription  gold_dist  \
0                          none                          none        NaN   
18                         none                          none        NaN   
43                         none                          none        NaN   
66                         none                          none        NaN   
93                         none                          none        NaN   

    length_accept reason  ... upstream_pointer  upstream_subject_id  user  \
0             NaN   none  ...               -1                 none     0   
18            NaN   none  ...               -1                 none     0   
43            NaN   none  ...               -1                 none     0   
66            NaN   none  ...               -1                 none     0   
93            NaN   none  ...               -1                 none     0   

                         user_candidate_transcription  \
0   each nonfiction book has a call number on its ...   
18  a dietitian goes to college for at least four ...   
43  the iris absorbs all of the light waves except...   
66  some acids you may know are vinegar and lemon ...   
93  the chase leads across a field toward a nearby...   

    user_comparison_transcription  user_dist  user_short word_distances  \
0                            none        NaN        none            NaN   
18                           none        NaN        none            NaN   
43                           none        NaN        none            NaN   
66                           none        NaN        none            NaN   
93                           none        NaN        none            NaN   

          unique_chain_identifier global_chain  
0   180419_AMT_lengthLimitedGPU_0            0  
18  180419_AMT_lengthLimitedGPU_0            0  
43  180419_AMT_lengthLimitedGPU_0            0  
66  180419_AMT_lengthLimitedGPU_0            0  
93  180419_AMT_lengthLimitedGPU_0            0  

[5 rows x 26 columns]

In [17]:
# take a 2-column subset of all_trials that we can put into R
input_output = all_runs[['gold_candidate_transcription','user_candidate_transcription','user',
                         'upstream_subject_id']]
#gold_candidate_transcription is what a participant heard
#user_candidate_transcription is what the participant produced

# remove the intitial sentences -- these are represnted as input for the first participant
%R -i input_output

/home/nwong/chompsky/serial_chain/telephone-analysis-public/telephone-env-3/lib/python3.7/site-packages/rpy2/robjects/pandas2ri.py:63: UserWarning: Error while trying to convert the column "gold_candidate_transcription". Fall back to string conversion. The error is: module 'pandas' has no attribute 'NA'
  % (name, str(e)))
/home/nwong/chompsky/serial_chain/telephone-analysis-public/telephone-env-3/lib/python3.7/site-packages/rpy2/robjects/pandas2ri.py:63: UserWarning: Error while trying to convert the column "user_candidate_transcription". Fall back to string conversion. The error is: module 'pandas' has no attribute 'NA'
  % (name, str(e)))
/home/nwong/chompsky/serial_chain/telephone-analysis-public/telephone-env-3/lib/python3.7/site-packages/rpy2/robjects/pandas2ri.py:63: UserWarning: Error while trying to convert the column "user". Fall back to string conversion. The error is: module 'pandas' has no attribute 'NA'
  % (name, str(e)))
/home/nwong/chompsky/serial_chain/telephone-analy

In [18]:
input_output

gold_candidate_transcription  \
0                                                  none   
1     each nonfiction book has a call number on its ...   
2     each non fiction book has a call number in its...   
3     Each nonfiction book had a call number on its ...   
4     each nonfiction book had a call number on its ...   
5     each non fiction book had a call number on its...   
6     each nonfiction book had a call number on its ...   
7     Each non fiction book had 12 numbers on its spine   
8     Each nonfiction book had twelve numbers on its...   
9     each non fiction book had twelve numbers on it...   
10    each nonfiction book had twelve notches on its...   
11    Each nonfiction book had twelve notches in its...   
12        which non fiction book would you want to read   
13         which nonfiction book would you like to read   
14            Which nonfiction book do you like to read   
15           which non fiction book do you like to read   
16           which non fiction book do you like to read   
17           which non fiction book do you like to read   
18                                                 none   
19    a dietitian goes to college for at least four ...   
20    a dietitian goes to college for at least four ...   
21     a priest goes to college for at least four years   
22     a priest goes to college for at least four years   
23    The priest goes to college for at least four y...   
24    The fruits lose their color for at least four ...   
25      the horses have color for at least four winters   
26          The horses are colorful and many have fluff   
27          the horses are colorful and many have fluff   
28             The horses are cold and need their fluff   
29               the horses are cold and need their hut   
...                                                 ...   
2222         But he found a very many of the same thing   
2223         have you found the very many of the saints   
2224              We found the very many of the saints    
2225                we found the very minimum of things   
2226              He follows the very minimum of things   
2227               he followed the very u haul of thing   
2228                                               none   
2229  he could see that they were determined to turn...   
2230  He could see that they were determined to turn...   
2231  he could see that they were determined to turn...   
2232  he could see that they already turned at the t...   
2233  You could see that he had already torn everyth...   
2234      You could see that he had torn everything off   
2235        you can see that he had torn everything off   
2236      You could see that he had torn everything off   
2237     You could see that she had torn everything off   
2238      We could see that she had torn everything off   
2239  Before you leave make sure you turn everything...   
2240  before you leave make sure you turn everything...   
2241  Before you leave make sure you turn everything...   
2242  before you leave make sure you turn everything...   
2243  Before you leave make sure you turn everything...   
2244  Before you leave make sure you turn everything...   
2245  Before you leave make sure you turn everything...   
2246  before you leave make sure you turn everything...   
2247  before you leave make sure you turn everything...   
2248  before you leave make sure you turn everything...   
2249  Before you leave make sure you turn everything...   
2250  Before you leave make sure you turn everything...   
2251  before you leave make sure you turn everything...   

                           user_candidate_transcription  \
0     each nonfiction book has a call number on its ...   
1     each non fiction book has a call number in its...   
2     each nonfiction book had a call number on its ...   
3     each nonfiction book had a call number on its ...   
4     each non fiction book had a call number on its...   
5     each non

In [19]:
%%R
source('getWordLevenshteinDistance.R')
print(paste(nrow(input_output), 'sentences'))
names(input_output) = c('input','output','output_subject','input_subject')  
input_output$input = tolower(as.character(input_output$input))
input_output$output = tolower(as.character(input_output$output))

computeEditTable = function(s,r,input_subject, output_subject){
    if (s == 'none'){
        # this is an initial sentence, return NA
        return(NA)
    } else {
        et = getReducedEditTable(s,r)
        # for python compatibility, use 0-indices
        et$sCounter = et$sCounter - 1
        et$rCounter = et$rCounter - 1
        et$input_subject = input_subject
        et$output_subject = output_subject
        return(et)
    }
}

editTables = mapply(computeEditTable, input_output$input, input_output$output,
                   input_output$input_subject, input_output$output_subject)

[1] "3193 sentences"


In [20]:
%%R
editTables[[2]] #this should correspond to wdf[,1]

   code      sWord   rWord sCounter rCounter
1     M       each    each        0        0
2     D nonfiction    <NA>        1       NA
3     I       <NA>     non       NA        1
4     I       <NA> fiction       NA        2
5     M       book    book        2        3
6     M        has     has        3        4
7     M          a       a        4        5
8     M       call    call        5        6
9     M     number  number        6        7
11    S         on      in        7        8
12    M        its     its        8        9
13    M      spine   spine        9       10
                                              sentence
1  each nonfiction book has a call number on its spine
2  each nonfiction book has a call number on its spine
3  each nonfiction book has a call number on its spine
4  each nonfiction book has a call number on its spine
5  each nonfiction book has a call number on its spine
6  each nonfiction book has a call number on its spine
7  each nonfiction book has a 

/home/nwong/chompsky/serial_chain/telephone-analysis-public/telephone-env-3/lib/python3.7/site-packages/rpy2/robjects/pandas2ri.py:63: UserWarning: Error while trying to convert the column "code". Fall back to string conversion. The error is: module 'pandas' has no attribute 'NA'
  % (name, str(e)))
/home/nwong/chompsky/serial_chain/telephone-analysis-public/telephone-env-3/lib/python3.7/site-packages/rpy2/robjects/pandas2ri.py:63: UserWarning: Error while trying to convert the column "sWord". Fall back to string conversion. The error is: Series can only be of one type, or None (and here we have <class 'str'> and <class 'rpy2.rinterface_lib.sexp.NACharacterType'>).
  % (name, str(e)))
/home/nwong/chompsky/serial_chain/telephone-analysis-public/telephone-env-3/lib/python3.7/site-packages/rpy2/robjects/pandas2ri.py:63: UserWarning: Error while trying to convert the column "rWord". Fall back to string conversion. The error is: Series can only be of one type, or None (and here we have <cla

In [21]:
%%R
print(computeEditTable('this is a', 'this is a mouse', NULL, NULL))
print(computeEditTable('this is a mouse', 'this is a', NULL, NULL ))
print(computeEditTable('this is a mouse', 'this is a mouse', NULL, NULL))
print(computeEditTable('this is a mouse', 'this is a house', NULL, NULL))

  code sWord rWord sCounter rCounter  sentence        response sLeftSequence
1    M  this  this        0        0 this is a this is a mouse              
2    M    is    is        1        1 this is a this is a mouse              
3    M     a     a        2        2 this is a this is a mouse     this is a
4    I  <NA> mouse       NA        3 this is a this is a mouse              
  rLeftSequence sRightSequence rRightSequence
1                    this is a      this is a
2                                  is a mouse
3     this is a                              
4    is a mouse                              
  code sWord rWord sCounter rCounter        sentence  response sLeftSequence
1    M  this  this        0        0 this is a mouse this is a              
2    M    is    is        1        1 this is a mouse this is a              
3    M     a     a        2        2 this is a mouse this is a     this is a
4    D mouse  <NA>        3       NA this is a mouse this is a    is a mouse


In [22]:
%%R
getDSMwrtInput = function(sentence_index, editTables){
    et = editTables[[sentence_index]]
    if (is.na(et)){
        return(data.frame(sentence_index, sCounter=NA,code=NA, input_subject=NA, output_subject=NA)) # these are initial sentences
    } else{
        et = editTables[[sentence_index]]    
        et$sentence_index = sentence_index
        # here is where insertions are removed so that we can join back with wfds
        return(subset(et, !is.na(sCounter))[,c('sentence_index','sCounter','code','input_subject','output_subject')])
    }
}

DSMwrtInput = do.call('rbind', lapply(c(1:length(editTables)), function(i){
    dsm = getDSMwrtInput(i, editTables)  
    if (!is.na(dsm)){
        dsm$sentence_index = dsm$sentence_index - 2 
        # -1 because Python indexes from 0
        # another -1 to bring the index of edits into alignment with the languag model results     
    } 
    return(dsm)
}))   

#DSMwrtInput = subset(DSMwrtInput, !is.na(code))

In [23]:
from rpy2.robjects import r, pandas2ri
pandas2ri.activate()
DSMwrtInput = r['DSMwrtInput']
DSMwrtInput.iloc[0:15,]

sentence_index  sCounter           code  \
1              -1.0       NaN  NA_character_   
110             0.0       0.0              M   
2               0.0       1.0              D   
5               0.0       2.0              M   
6               0.0       3.0              M   
7               0.0       4.0              M   
8               0.0       5.0              M   
9               0.0       6.0              M   
11              0.0       7.0              S   
12              0.0       8.0              M   
13              0.0       9.0              M   
111             1.0       0.0              M   
21              1.0       1.0              D   
3               1.0       2.0              D   
51              1.0       3.0              M   

                        input_subject                    output_subject  
1                       NA_character_                     NA_character_  
110                                 0  8cf6535ea0ae4addb28f5f90a2b13a7d  
2                                   0  8cf6535ea0ae4addb28f5f90a2b13a7d  
5                                   0  8cf6535ea0ae4addb28f5f90a2b13a7d  
6                                   0  8cf6535ea0ae4addb28f5f90a2b13a7d  
7                                   0  8cf6535ea0ae4addb28f5f90a2b13a7d  
8                                   0  8cf6535ea0ae4addb28f5f90a2b13a7d  
9                                   0  8cf6535ea0ae4addb28f5f90a2b13a7d  
11                                  0  8cf6535ea0ae4addb28f5f90a2b13a7d  
12                                  0  8cf6535ea0ae4addb28f5f90a2b13a7d  
13                                  0  8cf6535ea0ae4addb28f5f90a2b13a7d  
111  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
21   8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
3    8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
51   8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc

In [24]:
initialSentenceIndices = np.array(DSMwrtInput[np.isnan(DSMwrtInput.sCounter)]['sentence_index'].tolist())
wdf_initRemoved = wdf[(~wdf['sentence_index'].isin(initialSentenceIndices))]
DSMwrtInput_nansRemoved = DSMwrtInput[~np.isnan(DSMwrtInput.sCounter)]

In [25]:
print(DSMwrtInput_nansRemoved.shape[0])
print(wdf_initRemoved.shape[0])
#assert(DSMwrtInput_nansRemoved.shape[0] == wdf_initRemoved.shape[0])

27290
27298


In [26]:
wdf_initRemoved[wdf_initRemoved.sentence_index == 3192]

bnc_unigram_index  bnc_unigram_prob bnc_unigram_word  bnc_trigram_index  \
0                  0         -3.081292           before                  0   
1                  1         -2.186153              you                  1   
2                  2         -3.713525            leave                  2   
3                  3         -3.121925             make                  3   
4                  4         -3.643197             sure                  4   
5                  5         -2.186153              you                  5   
6                  6         -3.512815           change                  6   
7                  7         -3.763360       everything                  7   

   bnc_trigram_prob bnc_trigram_word roark_scores_prefix roark_scores_word  \
0         -3.037731           before              pfix:1            before   
1         -1.185921              you              pfix:2               you   
2         -1.507196            leave              pfix:3             leave   
3         -4.336845             make              pfix:4              make   
4         -1.549859             sure              pfix:5              sure   
5         -0.752118              you              pfix:6               you   
6         -3.870051           change              pfix:7            change   
7         -3.264657       everything              pfix:8        everything   

   roark_scores_prefix.1  roark_scores_srprsl  ...  gpt2_normal_scores_word  \
0                  6.993             3.037021  ...                   before   
1                 13.198             2.694363  ...                      you   
2                 20.940             3.362308  ...                    leave   
3                 30.850             4.303858  ...                     make   
4                 36.383             2.402951  ...                     sure   
5                 43.568             3.120406  ...                      you   
6                 54.143             4.593098  ...                   change   
7                 63.772             4.181822  ...               everything   

   gpt2_medium_scores_prob  gpt2_medium_scores_word  bert_scores_prob  \
0                -2.958956                   before         -0.451015   
1                -1.037076                      you         -0.024068   
2                -2.037063                    leave         -0.618477   
3                -3.606973                     make         -0.014824   
4                -0.028073                     sure         -0.003831   
5                -0.334407                      you         -0.122452   
6                -2.447857                   change         -3.240940   
7                -2.191092               everything         -1.073453   

   bert_scores_word  bart_scores_prob  bart_scores_word  sCounter  \
0            before         -0.520920            before         0   
1               you         -0.023925               you         1   
2             leave         -1.712257             leave         2   
3              make         -1.734913              make         3   
4              sure         -0.119730              sure         4   
5               you         -0.195653               you         5   
6            change         -2.139447            change         6   
7        everything         -2.241529        everything         7   

   sentence_index        word  
0            3192      before  
1            3192         you  
2            3192       leave  
3            3192        make  
4            3192        sure  
5            3192         you  
6            3192      change  
7            3192  everything  

[8 rows x 35 columns]

In [27]:
DSMwrtInput_nansRemoved[DSMwrtInput_nansRemoved.sentence_index == 3192] 

Empty DataFrame
Columns: [sentence_index, sCounter, code, input_subject, output_subject]
Index: []

In [28]:
dsm_counts = DSMwrtInput_nansRemoved.groupby(['sentence_index']).sCounter.agg(np.size).reset_index()

dsm_counts.columns = ['sentence_index', 'dsm_count']
wdf_counts = wdf_initRemoved.groupby('sentence_index').sCounter.agg(np.size).reset_index()
wdf_counts.columns = ['sentence_index', 'wdf_count']
count_check = wdf_counts.merge(dsm_counts, how='outer')
count_check # differences in the counts?
count_check['difference'] = count_check.wdf_count - count_check.dsm_count
count_check.sort_values(by=['difference'], ascending=False)

sentence_index  wdf_count  dsm_count  difference
0                  0         10       10.0         0.0
2003            2142          9        9.0         0.0
1994            2132          8        8.0         0.0
1995            2133          8        8.0         0.0
1996            2134          8        8.0         0.0
1997            2135          8        8.0         0.0
1998            2136          8        8.0         0.0
1999            2138         10       10.0         0.0
2000            2139          9        9.0         0.0
2001            2140         10       10.0         0.0
2002            2141         10       10.0         0.0
2004            2144         10       10.0         0.0
2015            2155          8        8.0         0.0
2005            2145         11       11.0         0.0
2006            2146         10       10.0         0.0
2007            2147         10       10.0         0.0
2008            2148          9        9.0         0.0
2009            2149          9        9.0         0.0
2010            2150          9        9.0         0.0
2011            2151          9        9.0         0.0
2012            2152          9        9.0         0.0
2013            2153          8        8.0         0.0
1993            2131          7        7.0         0.0
1992            2130          7        7.0         0.0
1991            2129          8        8.0         0.0
1990            2128          8        8.0         0.0
1971            2108          9        9.0         0.0
1972            2109         10       10.0         0.0
1973            2110         10       10.0         0.0
1974            2111         10       10.0         0.0
...              ...        ...        ...         ...
1024            1107         10       10.0         0.0
1025            1109         10       10.0         0.0
1026            1110          9        9.0         0.0
1027            1111          9        9.0         0.0
1028            1112          9        9.0         0.0
1009            1092         10       10.0         0.0
1007            1090         10       10.0         0.0
986             1068         10       10.0         0.0
1006            1089         10       10.0         0.0
987             1069          9        9.0         0.0
988             1070          9        9.0         0.0
989             1071          9        9.0         0.0
990             1072          9        9.0         0.0
991             1073          9        9.0         0.0
992             1074          9        9.0         0.0
993             1075          9        9.0         0.0
994             1076         10       10.0         0.0
995             1077         10       10.0         0.0
996             1078          9        9.0         0.0
997             1079          9        9.0         0.0
998             1080          9        9.0         0.0
999             1081          9        9.0         0.0
1000            1082          9        9.0         0.0
1001            1083          9        9.0         0.0
1002            1085         10       10.0         0.0
1003            1086         10       10.0         0.0
1004            1087         10       10.0         0.0
1005            1088         10       10.0         0.0
2998            3191          9        9.0         0.0
2999            3192          8        NaN         NaN

[3000 rows x 4 columns]

In [29]:
# merge DSMwrtInput into the word data frame
wdfr = wdf_initRemoved.merge(DSMwrtInput_nansRemoved) #sCounter is NaN for input sentences

In [30]:
#where did all my happy data go?
wdfr.code.value_counts()

M    22482
D     3442
S     1366
Name: code, dtype: int64

In [31]:
wdfr

bnc_unigram_index  bnc_unigram_prob bnc_unigram_word  \
0                      0         -3.310068             each   
1                      1         -7.309903       nonfiction   
2                      2         -3.631093             book   
3                      3         -2.600407              has   
4                      4         -1.681165                a   
5                      5         -3.737589             call   
6                      6         -3.321531           number   
7                      7         -2.162270               on   
8                      8         -2.804867              its   
9                      9         -5.034822            spine   
10                     0         -3.310068             each   
11                     1         -5.084593              non   
12                     2         -4.733100          fiction   
13                     3         -3.631093             book   
14                     4         -2.600407              has   
15                     5         -1.681165                a   
16                     6         -3.737589             call   
17                     7         -3.321531           number   
18                     8         -1.746052               in   
19                     9         -2.804867              its   
20                    10         -5.034822            spine   
21                     0         -3.310068             each   
22                     1         -7.309903       nonfiction   
23                     2         -3.631093             book   
24                     3         -2.385910              had   
25                     4         -1.681165                a   
26                     5         -3.737589             call   
27                     6         -3.321531           number   
28                     7         -2.162270               on   
29                     8         -2.804867              its   
...                  ...               ...              ...   
27260                  6         -3.701698             turn   
27261                  7         -3.763360       everything   
27262                  8         -3.181633              off   
27263                  0         -3.081292           before   
27264                  1         -2.186153              you   
27265                  2         -3.713525            leave   
27266                  3         -3.121925             make   
27267                  4         -3.643197             sure   
27268                  5         -2.186153              you   
27269                  6         -3.701698             turn   
27270                  7         -3.763360       everything   
27271                  8         -3.181633              off   
27272                  0         -3.081292           before   
27273                  1         -2.186153              you   
27274                  2         -3.713525            leave   
27275                  3         -3.121925             make   
27276                  4         -3.643197             sure   
27277                  5         -2.186153              you   
27278                  6         -3.701698             turn   
27279                  7         -3.763360       everything   
27280                  8         -3.181633              off   
27281                  0         -3.081292           before   
27282                  1         -2.186153              you   
27283                  2         -3.713525            leave   
27284                  3         -3.121925             make   
27285                  4         -3.643197             sure   
27286                  5         -2.186153              you   
27287                  6         -3.701698             turn   
27288                  7         -3.763360       everything   
27289                  8         -3.181633              off   

       bnc_trigram_index  bnc_trigram_prob bnc_trigram_word  \
0                      0         -2.9

# Merge With Word Properties

In [32]:
wdfr['word'] = wdfr['bnc_unigram_word']
lexiconch = pd.read_csv('data/lexiconch.csv', index_col=0)
print('Number of words before merging with Lexiconch: '+str(wdfr.shape[0]))
wdfl = wdfr.merge(lexiconch, how='left')
print('Number of words after merging with Lexiconch: '+str(wdfl.shape[0]))
' '.join(set(wdfr.word) - set(wdfl.word))

/home/nwong/chompsky/serial_chain/telephone-analysis-public/telephone-env-3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:2714: DtypeWarning: Columns (9,10,12,16) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


Number of words before merging with Lexiconch: 27290
Number of words after merging with Lexiconch: 27290


''

In [33]:
lexiconch.iloc[0]

word                               roadsweeper
conc_bigram                                  0
conc_conc_m                               4.85
conc_conc_sd                              0.37
conc_unknown                                 1
conc_total                                  27
conc_percent_known                        0.96
conc_subtlex                                 0
conc_dom_pos                                 0
kpm_alternative_spelling          road sweeper
kpm_freq_pm                                NaN
kpm_dom_pos_subtlex                        NaN
kpm_nletters                                11
kpm_nphon                                    8
kpm_nsyll                                    3
kpm_lemma_highest_pos              roadsweeper
kpm_aoa_kup                               9.83
kpm_perc_known                               1
kpm_aoa_kup_lem                           9.83
kpm_perc_known_lem                           1
kpm_aoa_bird_lem                          7.12
kpm_aoa_brist

In [34]:
yarkoni_pld = pd.read_table('data/pld20.txt', header=None)
yarkoni_pld.columns = ['word', 'pld20']

/home/nwong/chompsky/serial_chain/telephone-analysis-public/telephone-env-3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: read_table is deprecated, use read_csv instead, passing sep='\t'.
  """Entry point for launching an IPython kernel.


In [35]:
print('Number of words before merging with Yarkoni PLD: '+str(wdfl.shape[0]))
wdfy = wdfl.merge(yarkoni_pld, how='left')
print('Number of words after merging with Yarkoni PLD: '+str(wdfy.shape[0]))

Number of words before merging with Yarkoni PLD: 27290
Number of words after merging with Yarkoni PLD: 27290


In [36]:
subtlex = pd.read_csv('data/subtlex_augmented.csv')
subtlex['word'] = subtlex.Word
subtlex.iloc[0]

Word                         the
FREQcount                1501908
CDcount                     8388
FREQlow                  1339811
Cdlow                       8388
SUBTLWF                  29449.2
Lg10WF                    6.1766
SUBTLCD                      100
Lg10CD                    3.9237
ipa_                      [ð, ə]
ipa_single                [ð, ə]
ipa_diphthongs            [ð, ə]
unigram_probability    0.0302076
unigram_surprisal        3.49966
word                         the
Name: 0, dtype: object

In [37]:
print('Number of words before merging with Subtlex: '+str(wdfy.shape[0]))
wdfx = wdfy.merge(subtlex[['word','SUBTLCD']], how='left')
print('Number of words after merging with Subtlex: '+str(wdfx.shape[0]))

Number of words before merging with Subtlex: 27290
Number of words after merging with Subtlex: 27290


# Merge in Sentence Level Predictors

In [51]:
raw_sentence_data_path = './intermediate_results/all_runs_raw_model_outputs.csv'
all_runs_sentence = load_runs.postprocess_runs(raw_sentence_data_path)

all_runs_sentence['sentence_index'] = range(all_runs.shape[0])

Getting initial probabilities for biglm_probability
Getting initial probabilities for WSJ_Roark_Negative.Log.Probability
Getting initial probabilities for BNC_KNN_unigramProb
Getting initial probabilities for BNC_KNN_trigramProb
Getting initial probabilities for kenlm_probability
Getting initial probabilities for bllip_probability
Getting initial probabilities for bllip_wsj_probability
Getting initial probabilities for mikolov_wsj_probability
Getting initial probabilities for WSJ_gt_unigramProb
Getting initial probabilities for WSJ_gt_trigramProb
Getting initial probabilities for WSJ_gt_5gramProb
Getting initial probabilities for gpt2_normal_probability
Getting initial probabilities for gpt2_medium_probability
Getting initial probabilities for bert_probability
Getting initial probabilities for bart_probability


In [52]:
wdfs = wdfx.merge(all_runs_sentence, on='sentence_index')

In [53]:
wdfx.columns

Index(['bnc_unigram_index', 'bnc_unigram_prob', 'bnc_unigram_word',
       'bnc_trigram_index', 'bnc_trigram_prob', 'bnc_trigram_word',
       'roark_scores_prefix', 'roark_scores_word', 'roark_scores_prefix.1',
       'roark_scores_srprsl', 'roark_scores_SynSp', 'roark_scores_LexSp',
       'roark_scores_ambig', 'roark_scores_open', 'roark_scores_rernk',
       'roark_scores_toprr', 'roark_scores_stps', 'big_lm_scores_Unnamed: 0',
       'big_lm_scores_prob', 'big_lm_scores_word', 'kenlm_scores_prob',
       'kenlm_scores_preceding', 'kenlm_scores_unk', 'kenlm_scores_word',
       'gpt2_normal_scores_prob', 'gpt2_normal_scores_word',
       'gpt2_medium_scores_prob', 'gpt2_medium_scores_word',
       'bert_scores_prob', 'bert_scores_word', 'bart_scores_prob',
       'bart_scores_word', 'sCounter', 'sentence_index', 'word', 'code',
       'input_subject', 'output_subject', 'conc_bigram', 'conc_conc_m',
       'conc_conc_sd', 'conc_unknown', 'conc_total', 'conc_percent_known',
       'c

In [54]:
wdfs.loc[wdfs.sentence_index == 1][['bnc_unigram_word',
                                   'user_candidate_transcription',
                                    'gold_candidate_transcription',
                                    'input_subject',
                                    'output_subject'
                                   ]]

bnc_unigram_word                       user_candidate_transcription  \
10             each  each non fiction book has a call number in its...   
11              non  each non fiction book has a call number in its...   
12          fiction  each non fiction book has a call number in its...   
13             book  each non fiction book has a call number in its...   
14              has  each non fiction book has a call number in its...   
15                a  each non fiction book has a call number in its...   
16             call  each non fiction book has a call number in its...   
17           number  each non fiction book has a call number in its...   
18               in  each non fiction book has a call number in its...   
19              its  each non fiction book has a call number in its...   
20            spine  each non fiction book has a call number in its...   

                         gold_candidate_transcription  \
10  each nonfiction book has a call number on its ...   
11  each nonfiction book has a call number on its ...   
12  each nonfiction book has a call number on its ...   
13  each nonfiction book has a call number on its ...   
14  each nonfiction book has a call number on its ...   
15  each nonfiction book has a call number on its ...   
16  each nonfiction book has a call number on its ...   
17  each nonfiction book has a call number on its ...   
18  each nonfiction book has a call number on its ...   
19  each nonfiction book has a call number on its ...   
20  each nonfiction book has a call number on its ...   

                       input_subject                    output_subject  
10  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
11  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
12  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
13  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
14  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
15  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
16  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
17  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
18  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
19  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc  
20  8cf6535ea0ae4addb28f5f90a2b13a7d  edf8f705ab7241a191fa3ae24e381ebc

# Save the output

In [56]:
wdfs.to_csv('output/wordLevelChanges.csv', index=False)

In [57]:
for col in wdfs.columns:
    print(col)

bnc_unigram_index
bnc_unigram_prob
bnc_unigram_word
bnc_trigram_index
bnc_trigram_prob
bnc_trigram_word
roark_scores_prefix
roark_scores_word
roark_scores_prefix.1
roark_scores_srprsl
roark_scores_SynSp
roark_scores_LexSp
roark_scores_ambig
roark_scores_open
roark_scores_rernk
roark_scores_toprr
roark_scores_stps
big_lm_scores_Unnamed: 0
big_lm_scores_prob
big_lm_scores_word
kenlm_scores_prob
kenlm_scores_preceding
kenlm_scores_unk
kenlm_scores_word
gpt2_normal_scores_prob
gpt2_normal_scores_word
gpt2_medium_scores_prob
gpt2_medium_scores_word
bert_scores_prob
bert_scores_word
bart_scores_prob
bart_scores_word
sCounter
sentence_index
word
code
input_subject
output_subject
conc_bigram
conc_conc_m
conc_conc_sd
conc_unknown
conc_total
conc_percent_known
conc_subtlex
conc_dom_pos
kpm_alternative_spelling
kpm_freq_pm
kpm_dom_pos_subtlex
kpm_nletters
kpm_nphon
kpm_nsyll
kpm_lemma_highest_pos
kpm_aoa_kup
kpm_perc_known
kpm_aoa_kup_lem
kpm_perc_known_lem
kpm_aoa_bird_lem
kpm_aoa_bristol_lem
kp

See R notebook, Error Prediction Model - Logistic Regression